In [1]:
# !pip install folium
# !pip install geojson

In [4]:
import os
import pandas as pd
import numpy as np
import folium
import geojson


In [9]:
prop_df = pd.read_csv('data/Property_Valuation_and_Assessment_Data.csv')

In [10]:
print("full data shape", prop_df.shape)
print("data with FULLVAL", len(prop_df['FULLVAL']))

full data shape (9845857, 40)
data with FULLVAL 9845857


In [11]:
prop_df['TAXCLASS'].unique()

array(['2', '4', '3', '1B', '2B', '2C', '1A', '1', '1C', '2A', '1D'],
      dtype=object)

In [12]:
# keep residential prop
prop_df = prop_df[~prop_df['TAXCLASS'].isin(['3', '4'])]
prop_df.shape

(8818781, 40)

In [13]:
# change year to number
def yr(year):
    yr = year[:2]+year[-2:]
    return int(yr)

yr('2011/1012')

2012

In [14]:
# total prop values:
prop_val = prop_df.groupby('YEAR')['FULLVAL'].sum().reset_index()
prop_val['YEAR']=prop_val['YEAR'].apply(lambda year: yr(year))
prop_val['pct_change'] = prop_val['FULLVAL'].pct_change()*100
prop_val

YEAR       FULLVAL  pct_change
0  2011  605165681141         NaN
1  2012  610525608939    0.885696
2  2013  624447793860    2.280361
3  2014  630166042578    0.915729
4  2015  665008693142    5.529122
5  2016  716322878935    7.716318
6  2017  796593256432   11.205893
7  2018  866736019655    8.805342
8  2019  953353291587    9.993501

In [15]:
# number of prop by year
num_prop = prop_df.groupby('YEAR')['FULLVAL'].count().reset_index()
num_prop.columns = ['YEAR', 'Property_Count']
num_prop['YEAR']=num_prop['YEAR'].apply(lambda year: yr(year))
num_prop['pct_change'] = num_prop['Property_Count'].pct_change()*100
num_prop

YEAR  Property_Count  pct_change
0  2011          962046         NaN
1  2012          968881    0.710465
2  2013          972823    0.406861
3  2014          974321    0.153985
4  2015          978747    0.454265
5  2016          981316    0.262478
6  2017          987502    0.630378
7  2018          993613    0.618834
8  2019          999532    0.595705

number of properties increases;
tot values increases more over the last 5 years

explore borough next

In [16]:
prop_val_boro = prop_df.groupby(['BORO', 'YEAR'])['FULLVAL'].sum().reset_index()
prop_val_boro['YEAR']=prop_val_boro['YEAR'].apply(lambda year: yr(year))
prop_val_boro=prop_val_boro.assign(pct_change=prop_val_boro.groupby(['BORO'])['FULLVAL'].pct_change()*100)
prop_val_boro.to_csv('data/prop_val_boro.csv')

In [17]:
num_prop_boro = prop_df.groupby(['BORO','YEAR'])['FULLVAL'].count().reset_index()
num_prop_boro.columns = ['BORO','YEAR', 'Property_Count']
num_prop_boro['YEAR']=num_prop_boro['YEAR'].apply(lambda year: yr(year))
num_prop_boro=num_prop_boro.assign(pct_change=num_prop_boro.groupby(['BORO'])['Property_Count'].pct_change()*100)
num_prop_boro.to_csv('data/num_prop_boro.csv')

next: explore by ntas

In [18]:
prop_val_nta = prop_df.groupby(['NTA', 'YEAR'])['FULLVAL'].sum().reset_index()
prop_val_nta['YEAR']=prop_val_nta['YEAR'].apply(lambda year: yr(year))
prop_val_nta=prop_val_nta.assign(pct_change=prop_val_nta.groupby(['NTA'])['FULLVAL'].pct_change()*100)
prop_val_nta.to_csv('data/prop_val_nta.csv')

In [19]:
num_prop_nta = prop_df.groupby(['NTA','YEAR'])['FULLVAL'].count().reset_index()
num_prop_nta.columns = ['NTA','YEAR', 'Property_Count']
num_prop_nta['YEAR']=num_prop_nta['YEAR'].apply(lambda year: yr(year))
num_prop_nta=num_prop_nta.assign(pct_change=num_prop_nta.groupby(['NTA'])['Property_Count'].pct_change()*100)
num_prop_nta.to_csv('data/num_prop_nta.csv')

by zip code

In [20]:
prop_val_zip = prop_df.groupby(['POSTCODE', 'YEAR'])['FULLVAL'].sum().reset_index()
prop_val_zip['YEAR']=prop_val_zip['YEAR'].apply(lambda year: yr(year))
prop_val_zip=prop_val_zip.assign(pct_change=prop_val_zip.groupby(['POSTCODE'])['FULLVAL'].pct_change()*100)
prop_val_zip.to_csv('data/prop_val_zip.csv')

In [21]:
num_prop_zip = prop_df.groupby(['POSTCODE','YEAR'])['FULLVAL'].count().reset_index()
num_prop_zip.columns = ['POSTCODE','YEAR', 'Property_Count']
num_prop_zip['YEAR']=num_prop_zip['YEAR'].apply(lambda year: yr(year))
num_prop_zip=num_prop_zip.assign(pct_change=num_prop_zip.groupby(['POSTCODE'])['Property_Count'].pct_change()*100)
num_prop_zip.to_csv('data/num_prop_zip.csv')

In [23]:
# open geojson file about the borders of provinces
with open('data/Neighborhood Tabulation Areas (NTA).geojson') as f:
    gj = geojson.load(f)
    
m = folium.Map(location=[40.7, -74], zoom_start=10)

folium.Choropleth(
    data=prop_val_nta[prop_val_nta['YEAR']==2018],
    geo_data=gj,
    name="choropleth",
    columns=["NTA","pct_change"],
    key_on="properties.ntaname",
    fill_color="Blues",
    fill_opacity=.7,
    line_opacity=1,
    nan_fill_color='white',
    legend_name="Prop % change"
).add_to(m)

m

In [24]:
prop_val_zip

POSTCODE  YEAR     FULLVAL  pct_change
0       1239.0  2016      184800         NaN
1       1239.0  2017      184800    0.000000
2      10001.0  2011  2580649524         NaN
3      10001.0  2012  2910247399   12.771896
4      10001.0  2013  3097365754    6.429637
...        ...   ...         ...         ...
1724   33803.0  2012      475000    0.000000
1725   33803.0  2013      451000   -5.052632
1726   33803.0  2014      396000  -12.195122
1727   33803.0  2015      396000    0.000000
1728   33803.0  2016      396000    0.000000

[1729 rows x 4 columns]